Informatics 2 - Foundations of Data Science

# Clustering with K-means and basic Hierarchical clustering

David Sterratt, 2020-2024

In [ ]:
import pandas as pd
import seaborn as sns
import numpy as np
import scipy
import matplotlib.pyplot as plt
import matplotlib
from scipy.cluster import hierarchy

matplotlib.rcParams['savefig.dpi'] = 300
matplotlib.rcParams['font.size'] = 12
matplotlib.rcParams['figure.figsize'] = [3, 3]

## Load data
We'll use the [oranges and lemons data set](http://homepages.inf.ed.ac.uk/imurray2/teaching/oranges_and_lemons/) collected by Iain Murray.

In [ ]:
dat = pd.read_csv('fruits.csv')
dat.head()

In [ ]:
fig = plt.figure(figsize=(5, 5))
ax = sns.scatterplot(x='Width (cm)', y='Height (cm)', data=dat)
ax.set_aspect(1)
ax.set_xlim([2, 10])
plt.tight_layout()
#fig.savefig('fruit-raw.png')
#fig.savefig('fruit-raw.pdf')

##  Functions to perform K-means clustering

In [ ]:
def sqdist(m, x):
    n = x.shape[0]
    D = x.shape[1]
    K = m.shape[0]
    sumsq = np.zeros((n, K))
    for i in range(D):
        sumsq = sumsq + np.power(np.subtract.outer(x[:,i], m[:,i]), 2)
    return(sumsq)

def kmeans(x, K, maxiter, verbose=True):
    n = x.shape[0]
    D = x.shape[1]
    
    ## Initialisation
    
    # Choose random data points as cluster centres
    m = x[np.random.choice(range(n), K, replace=False), :]
    sqd = sqdist(x, m)
    c = sqd.argmin(0)
        
    i = 0
    converged = False
    c0 = np.zeros(n)
    ## Iterate
    while (not converged) and (i < maxiter):
        i = i + 1
        ## Assign each point to closest cluster centre

        ## Compute distances
        sqd = sqdist(x, m)
        c = sqd.argmin(0)

        ## Recompute means
        for k in range(K):
            m[k,:] = np.mean(x[k == c,:], 0)     
        
        if ((c0 == c).all()):
            if verbose:
                print("Converged after " + str(i) + " iterations")
            converged = True
            
        c0 = c.copy() ## Keep copy of old cluster assignments to check for convergence

    return((c, m))

def kmeans_iteration(x, m):
    K = m.shape[0]
    
    ## Compute distances
    sqd = sqdist(x, m)
    c = sqd.argmin(0)

    ## Recompute means
    for k in range(K):
        m[k,:] = np.mean(x[k == c,:], 0)
    
    return((c, m))

## Cluster the data

Our K-means algorithm doesn't standardise the data, so we need to do this ourselves first.

In [ ]:
x = dat[['Width (cm)', 'Height (cm)']].to_numpy()
z = (x - x.mean(0))/x.std(0)

In [ ]:
dat['Cluster'], zbar = kmeans(z, 5, 100)
xbar = pd.DataFrame(zbar*np.array(x.std()) + np.array(x.mean()), columns = ['Width (cm)', 'Height (cm)'])
xbar['Cluster'] = list(range(xbar.shape[0]))

In [ ]:
fig = plt.figure(figsize=(5, 5))
ax = sns.scatterplot(x='Width (cm)', y='Height (cm)', hue='Cluster', style='Cluster', data=dat,
                     palette='colorblind')
# sns.scatterplot(x=xbar[:,0], y=xbar[:,1], color='black', data=dat, palette='colorblind')
ax.set_xlim([2, 10])
ax.set_aspect(1)


# plt.legend(bbox_to_anchor=(1.01, 1),borderaxespad=0)
plt.tight_layout()
##fig.savefig('fruit-clustered.png')
##fig.savefig('fruit-clustered.pdf')

sns.scatterplot(x='Width (cm)', y='Height (cm)', color='black', style='Cluster', data=xbar, palette='colorblind',
               legend=False, sizes=(150,150), size='Cluster', alpha=0.5)
##fig.savefig('fruit-clustered-with-centres.png')

In [ ]:
fig = plt.figure(figsize=(5, 5))

ax = sns.scatterplot(x='Width (cm)', y='Height (cm)', hue='Fruit', style='Fruit', data=dat, palette='colorblind')
# plt.legend(bbox_to_anchor=(1.01, 1),borderaxespad=0)
ax.set_xlim([2, 10])
ax.set_aspect(1)
ax.legend(loc='upper left')
plt.tight_layout()

#fig.savefig('fruit-original.png')
#fig.savefig('fruit-original.pdf')

## Kmeans step-by-step

In [ ]:
def sum_sq_err(m, x, c):
    n = x.shape[0]
    E = 0
    for i in range(n):
        E = E + np.sum(np.power(x[i,:] - m[c[i],:], 2))
    return(E)

def plot_kmeans(c, zbar, z):
    fig = plt.figure(figsize=(5, 5))
    ax = sns.scatterplot(x=z[:,0], y=z[:,1], hue=c, style=c, palette='colorblind')
    sns.scatterplot(x=zbar[:,0], y=zbar[:,1], color='black', style=list(range(zbar.shape[0])),
                        palette='colorblind', legend=False, sizes=(150,150), size=2, alpha=0.5)
    ax.set_xlim([-3, 3])
    ax.set_ylim([-3, 3])
    ax.set_aspect(1)
    plt.annotate("E = " + '%3.2f'%(sum_sq_err(zbar, z, c)), (1, -2.5))
    plt.xlabel('Width')
    plt.ylabel('Height')
    plt.tight_layout()


x = dat[['Width (cm)', 'Height (cm)']].to_numpy()
z = (x - x.mean(0))/x.std(0)
c, zbar = kmeans(z, 5, 0)
i = 1
plot_kmeans(c, zbar, z)
plt.savefig('iteration' + str(i) + '.png')

In [ ]:
i = i + 1
c, zbar = kmeans_iteration(z, zbar)
plot_kmeans(c, zbar, z)
plt.savefig('iteration' + str(i) + '.png')

In [ ]:
c, zbar = kmeans_iteration(z, zbar)
plot_kmeans(c, zbar, z)

In [ ]:
c, zbar = kmeans_iteration(z, zbar)
plot_kmeans(c, zbar, z)

In [ ]:
c, zbar = kmeans_iteration(z, zbar)
plot_kmeans(c, zbar, z)

In [ ]:
c, zbar = kmeans_iteration(z, zbar)
plot_kmeans(c, zbar, z)

## Evaluation of Kmeans

In [ ]:
c, zbar = kmeans(z, 5, 10)
plot_kmeans(c, zbar, z)
# plt.savefig('kmeans-evaluation1.png')
# plt.savefig('kmeans-evaluation1.pdf')

In [ ]:
c, zbar = kmeans(z, 5, 10)
plot_kmeans(c, zbar, z)
# plt.savefig('kmeans-evaluation2.png')
# plt.savefig('kmeans-evaluation2.pdf')

## Multiple attempts

In [ ]:
def kmeans_multiple(z, K, maxiter, n_attempts):
    c0, zbar0 = kmeans(z, K, maxiter, False)
    E0 = sum_sq_err(zbar0, z, c0)
    for i in range(n_attempts):
        c, zbar = kmeans(z, K, maxiter, False)
        E = sum_sq_err(zbar0, z, c0)
        if E < E0:
            c0 = c.copy()
            zbar0 = zbar.copy()
            E0 = E
    return(c0, zbar0, E0)

def scree(z, Ks, maxiter, n_attempts):
    E = np.zeros(len(Ks))
    for i in range(len(Ks)):
        c, zbar, E[i] = kmeans_multiple(z, Ks[i], maxiter, n_attempts)
    return(pd.DataFrame({'K': Ks, 'E': E}))

out = scree(z, np.arange(1, 7), 10, 1000)
out

In [ ]:
plt.figure(figsize=[4, 3])
sns.lineplot(x='K', y='E', data=out)
plt.ylim([0, 120])
plt.annotate('Elbow', (5, 13))
plt.tight_layout()
plt.savefig('kmeans-scree.png')

## Hierarchical clustering

In [ ]:
plt.figure(figsize=(10, 11))
hc = hierarchy.linkage(x, 'centroid')
hierarchy.dendrogram(hc, orientation='right', labels=np.array(dat.Type), leaf_font_size=10,
                    color_threshold=1.0)
plt.xlabel('Inter-cluster distance')

plt.tight_layout()
plt.savefig('fruit-hierarchical.png')
plt.savefig('fruit-hierarchical.pdf')

plt.show()